In [ ]:
from google.colab import drive
drive.mount("/content/drive", force_remount=True)

Mounted at /content/drive


In [ ]:
!pip3 install transformers
!pip3 install simpletransformers

import pandas as pd
from simpletransformers.language_modeling import LanguageModelingModel
from simpletransformers.classification import ClassificationModel, ClassificationArgs

import torch
from torch.utils.data import Dataset, DataLoader

import dill
import logging

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 20.2 MB/s eta 0:00:00
ERROR: Operation cancelled by user
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 250.7/250.7 kB 1.8 MB/s eta 0:00:00
  Using cached transformers-4.28.1-py3-none-any.whl (7.0 MB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 474.6/474.6 kB 24.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 779.5 kB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 11.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 14.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.9/8.9 MB 15.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 20.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━

ModuleNotFoundError: ignored

In [ ]:
!unzip "/content/drive/MyDrive/472 Project Files/Trained Models/Electra.zip" -d "/content/electra"

unzip:  cannot find or open /content/drive/MyDrive/472 Project Files/Trained Models/Electra.zip, /content/drive/MyDrive/472 Project Files/Trained Models/Electra.zip.zip or /content/drive/MyDrive/472 Project Files/Trained Models/Electra.zip.ZIP.


In [ ]:
!unzip "/content/drive/MyDrive/472 Project Files/Trained Models/MedElectra.zip" -d "/content/medelectra"

unzip:  cannot find or open /content/drive/MyDrive/472 Project Files/Trained Models/MedElectra.zip, /content/drive/MyDrive/472 Project Files/Trained Models/MedElectra.zip.zip or /content/drive/MyDrive/472 Project Files/Trained Models/MedElectra.zip.ZIP.


In [ ]:
!unzip "/content/drive/MyDrive/472 Project Files/Trained Models/Roberta.zip" -d "/content/roberta"

unzip:  cannot find or open /content/drive/MyDrive/472 Project Files/Trained Models/Roberta.zip, /content/drive/MyDrive/472 Project Files/Trained Models/Roberta.zip.zip or /content/drive/MyDrive/472 Project Files/Trained Models/Roberta.zip.ZIP.


In [ ]:
!unzip "/content/drive/MyDrive/472 Project Files/Trained Models/biobert_2_epch.zip" -d "/content/biobert"

Archive:  /content/drive/MyDrive/472 Project Files/Trained Models/biobert_2_epch.zip
replace /content/biobert/content/outputs/checkpoint-43713-epoch-3/training_args.bin? [y]es, [n]o, [A]ll, [N]one, [r]ename: 

In [ ]:
!unzip "/content/drive/MyDrive/472 Project Files/Trained Models/saved_model_distil_ro_berta.zip" -d "/content/distilled_roberta"

Archive:  /content/drive/MyDrive/472 Project Files/Trained Models/saved_model_distil_ro_berta.zip
replace /content/distilled_roberta/content/outputs/checkpoint-43713-epoch-3/training_args.bin? [y]es, [n]o, [A]ll, [N]one, [r]ename: 

# Code

In [ ]:
import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

import matplotlib.pyplot as plt
import numpy as np

plt.style.use("ggplot")

np.random.seed(1)
torch.manual_seed(1)
torch.cuda.manual_seed(1)

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [ ]:
import os

def get_model_folder(model_name, base_folder="/content/"):
  location = f"{base_folder}{model_name}/content/outputs"
  checkpoint_folder = os.listdir(location)[0]
  return f"{location}/{checkpoint_folder}"

#get_model_folder("electra")

In [ ]:
class TransformerEnsemble(nn.Module):
  def __init__(self):
      model_args = ClassificationArgs(num_train_epochs=4)
      #folder = "/content/drive/MyDrive/472 Project Files/Trained Models/"
      
      kwargs = {"num_labels": 40, "args": model_args, 
                "use_cuda": torch.cuda.is_available()}
      super(TransformerEnsemble, self).__init__()

      self.models = [
        ClassificationModel("electra", get_model_folder("electra"), **kwargs), #Electra
        ClassificationModel("electra", get_model_folder("medelectra"), **kwargs), #MedElectra
        #ClassificationModel("bert", folder+"bert", **kwargs), #BERT
        ClassificationModel("bert", get_model_folder("biobert"), **kwargs), #BioBERT
        ClassificationModel("roberta", get_model_folder("roberta"), **kwargs), #RoBERTa
        ClassificationModel("roberta", get_model_folder("distilled_roberta"), **kwargs), #DistilledRoBERTa
      ]

    
      self.num_models = len(self.models)
      num_outputs = 40

      # Freeze the weights of the model
      """
      for model in self.models:
        for param in model.parameters():
          param.requires_grad = False
      """

      # TODO what should be the dimensions?
      self.classifier = nn.Linear(self.num_models*num_outputs, num_outputs)
      self.softmax = nn.Softmax(dim=1)

    
  # https://discuss.pytorch.org/t/combining-trained-models-in-pytorch/28383/15
  def forward(self, sentence):
    # Classify the sentence from all of the models
    classifs = []
    for model in self.models:
      result, model_outputs = model.predict(sentence)
      classifs.append(torch.from_numpy(model_outputs))

    x = torch.cat(classifs, dim=1).float()
    x = self.softmax(self.classifier(F.relu(x)))
    return x

In [ ]:
class TextDataset(Dataset):
  def __init__(self, text_list, label_list, device):
    """Takes in numpy arrays as input."""
    # TODO: replace with tensors
    self.text = text_list
    self.labels = label_list
    
  def __len__(self):
    return (self.labels.shape[0])

  def __getitem__(self, index):
    label = self.labels[index]
    text = self.text[index]
    # Convert label to one-hot encoded vector
    label_vector = torch.zeros(40)
    label_vector[label] = 1
    # Return 
    return (text, label_vector)

In [ ]:
def dataloader_from_file(filename):
  """TEMPORARY: Replace with k-fold validation thing later"""

  base = "/content/drive/MyDrive/472 Project Files/Stratified Input Data/"  
  #df = pd.read_csv(base + filename)
  df = pd.read_csv(base + filename)

  # Remove NaNs
  are_text_strings = df.applymap(lambda x: isinstance(x, (str)))['text']
  df = df[are_text_strings][:20]

  text_list = df['text'].to_numpy()
  label_list = df['label'].to_numpy()
  TD = TextDataset(text_list, label_list, device)
  print(TD.text.shape)
  return TD

In [ ]:
# Load model & data
model = TransformerEnsemble()
#TODO get device working
# model.to(device)

In [ ]:
train_set = dataloader_from_file("ensemble_df-2.csv")
train_dataloader = DataLoader(train_set, batch_size=1, shuffle=True)

val_set = dataloader_from_file("eval_df-3.csv")
val_dataloader = DataLoader(train_set, batch_size=1, shuffle=True)

test_set = dataloader_from_file("train_df-2.csv")
test_dataloader = DataLoader(test_set, batch_size=1, shuffle=True)

(20,)
(20,)
(20,)


In [ ]:
loss_function = nn.BCELoss()
optimizer = optim.Adam(model.parameters(), lr=1e-3, weight_decay=0.001)
#scheduler = torch.optim.lr_scheduler.CosineAnnealingWarmRestarts(optimizer, T_0 = 5)
num_epochs = 10

In [ ]:
train_losses, val_losses = [], []
train_accs, val_accs = [], []

In [ ]:
def train(model):
  for epoch in range(num_epochs):
    train_loss, val_loss = [], []
    train_correct, train_count = 0, 0
    val_correct, val_count = 0, 0

    for idx, batch in enumerate(train_dataloader):
      ## Fetch inputs and labels from batch
      sentences, labels = batch
      #sentences = sentences.to(device)
      #labels = labels.to(device)
      pred = model(list(sentences))
      loss = loss_function(pred, labels)
      
      optimizer.zero_grad()
      loss.backward()
      optimizer.step()

      ## Compute accuracy and track accuracy and loss
      train_loss.append(loss.item())
      train_correct += sum(pred == labels)
      train_count += 1

    train_acc = torch.Tensor.cpu(train_correct / train_count)

    # Validation phase
    model.eval() 
    for idx, batch in enumerate(val_dataloader):
      with torch.no_grad():
        sentences, labels = batch
        #sentences = sentences.to(device)
        #labels = labels.to(device)

        pred = model(list(sentences))
        loss = loss_function(pred, labels)

        val_loss.append(loss.item())
        val_correct += sum(pred == labels)
        val_count += 1

    val_acc = torch.Tensor.cpu(val_correct / val_count)

    # Added a scheduler
    val_loss_mean = np.mean(val_loss)
    train_loss_mean = np.mean(train_loss)
    #scheduler.step(val_loss_mean) #For Plateau LR scheduler
    #scheduler.step() # For StepLR / CosineAnnealing scheduler

    print("Epoch : {}, Train loss: {}, train accuracy: {}, Val loss: {}, val accuracy: {}".
          format(epoch, np.mean(train_loss), train_acc, np.mean(val_loss), val_acc))

    train_losses.append(train_loss_mean)
    val_losses.append(val_loss_mean)
    train_accs.append(train_acc)
    val_accs.append(val_acc)

In [ ]:
train(model)

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]